### Preprocess the data

Next, we need to transform our simulation data into .csv files containing the data we need for our simulations. We can do that using the `preprocess_file` function in the file `preprocess.py`.

In [1]:
import os
import shutil

from spatz.utils.preprocess import preprocess_file


PATH = 'data/simulations/'

# Delete the old folder of preprocessed files.
if os.path.isdir(PATH + 'temp/'):
    shutil.rmtree(PATH + 'temp/')

# Create the folder again.
os.mkdir(PATH + 'temp/')

# Preprocess the files.
for file in os.listdir(PATH):
    if not os.path.isdir(PATH + file) and '.txt' in file:
        df = preprocess_file(PATH + file)
        df.to_csv(PATH + 'temp/' + file.replace('.txt', '.csv'))

### Setup the simulation

First we have to create a simulation instance and specify how we want to iterate through the simulation. We choose to sample data every 0.1 seconds.

In addition, there is the option to add delays in the sampling by adding Gaussian noise to the sampling rate. In this case data might be sampled after 0.1 + noise seconds.

In [2]:
from spatz.simulation import Simulation, UniformTimeSteps

# Construct a time model.
timesteps = UniformTimeSteps(0.1, mu=0, sigma=0, delay_only=True)

# Construct a simulation instance with the time model.
simulation = Simulation(timesteps)

Next, we need to specify the sensors we are using. For this demo we are using the sensors used by Aquila's CAPUT v4. We call `simulation.add_sensor` with the sensor class as an argument to register and create a sensor for the simulation. This allows the sensor to fetch the data.

In [3]:
from spatz.sensors.imu.wsen_isds import WSEN_ISDS_ACC, WSEN_ISDS_GYRO
from spatz.sensors.pressure.ms5611_01ba03 import MS5611_01BA03

press_sensor = simulation.add_sensor(MS5611_01BA03)

# Use the offset argument to change the position of the imu in relation to the rocket's center of gravity.
accelerometer = simulation.add_sensor(WSEN_ISDS_ACC, offset=0)
gyro = simulation.add_sensor(WSEN_ISDS_GYRO, offset=0)

### Run the simulation

With everything set up, we can load the dataset we want to explore.

In [4]:
simulation.load(PATH + 'temp/' + '7km.csv')

The simulation class has a function `run` which allows us to loop through every time step. The returned values are the index of the current step, the time of the current step and the change in time since the last time step.

In each iteration we can call the sensors like functions to obtain the measurements at the current time steps. Please note that calling sensors multiple times at the same time steps may result in different measurements.

In [5]:
logger = simulation.get_logger()

# Set verbose to False to disable the progress bar
for step, t, dt in simulation.run(verbose=True):
    # Get the sensor data for the current time
    press = press_sensor()
    acc = accelerometer()
    rot_rate = gyro()

    # TODO: Add your computation here.

ModuleNotFoundError: No module named 'kalman'

In [ ]:
df = logger.get_dataframe()

df

### Do your research

In [ ]:
import matplotlib.pyplot as plt

In [ ]:
plt.plot(df['time'][1:], df['mach/mach_no'][1:], label='mach number')
plt.plot(df['time'][1:], df['MS5611_01BA03/ts_effects'][1:], label='ts effects')
plt.show()

In [ ]:
plt.plot(df['mach/mach_no'][1:], df['MS5611_01BA03/ts_effects'][1:])
plt.show()

In [ ]:
plt.plot(df['time'][1:], df['MS5611_01BA03/pressure'][1:])
plt.show()

In [ ]:
plt.plot(df['time'], df['WSEN_ISDS/acc_x'], label='x')
plt.plot(df['time'], df['WSEN_ISDS/acc_y'], label='y')
plt.plot(df['time'], df['WSEN_ISDS/acc_z'], label='z')
plt.legend()
plt.show()